# Introduction

We use char2char NLM using seq2seq + Attention model.

The encoder-decoder follows seq2seq model.

The decoding is based on attending to the encoder + the current decoder state.
The attention model follows: Luong et al., 2015 (https://arxiv.org/abs/1508.04025) instead of the traditional Bahadanau et al., 2014 (https://arxiv.org/abs/1409.0473). The implementation of attention follows this blog: https://wanasit.github.io/attention-based-sequence-to-sequence-in-keras.html. The reason to choose that is that the attention level is working at the output level of the LSTM, while Bahdanau attention needs to work at the state level of the encoder.

Planning to move to Attention() layer from fast.ai Jeremy Howard implementation: https://github.com/fastai/courses/blob/master/deeplearning2/attention_wrapper.py, which is following Bahdanau attention. 

# Imports

In [1]:
from __future__ import print_function
import tensorflow as tf
import keras.backend as K
from keras.backend.tensorflow_backend import set_session
from keras.models import Model
from keras.layers import Input, LSTM, Dense, Bidirectional, Concatenate, GRU, Dot, TimeDistributed, Activation, Embedding
from keras import optimizers
from keras.callbacks import ModelCheckpoint, TensorBoard, LearningRateScheduler
import numpy as np
import os
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt
import seaborn as sns
import json
from nltk.tokenize import word_tokenize
from utils import *
import pdb
%matplotlib inline

Using TensorFlow backend.


In [2]:

gpu_alloc("1")

# Load data

In [3]:
data_path = '.'
file_name = 'wonderland.txt'

In [4]:
num_samples = 100000
full_file_name = os.path.join(data_path, file_name)
raw_texts = load_data(full_file_name, num_samples)
print(raw_texts[:200])

["ALICE'S ADVENTURES IN WONDERLAND\n", '\n', 'Lewis Carroll\n', '\n', 'THE MILLENNIUM FULCRUM EDITION 3.0\n', '\n', 'CHAPTER I. Down the Rabbit-Hole\n', '\n', 'Alice was beginning to get very tired of sitting by her sister on the\n', 'bank, and of having nothing to do: once or twice she had peeped into the\n', 'book her sister was reading, but it had no pictures or conversations in\n', "it, 'and what is the use of a book,' thought Alice 'without pictures or\n", "conversations?'\n", '\n', 'So she was considering in her own mind (as well as she could, for the\n', 'hot day made her feel very sleepy and stupid), whether the pleasure\n', 'of making a daisy-chain would be worth the trouble of getting up and\n', 'picking the daisies, when suddenly a White Rabbit with pink eyes ran\n', 'close by her.\n', '\n', 'There was nothing so VERY remarkable in that; nor did Alice think it so\n', "VERY much out of the way to hear the Rabbit say to itself, 'Oh dear!\n", "Oh dear! I shall be late!' (when s

In [5]:


in_seq_len = 20
out_seq_len = 20
input_texts, target_texts = generate_lm_data(raw_texts, in_seq_len, out_seq_len)

In [6]:
# Sample data
print(len(input_texts))
for i in range(10):
    print(input_texts[i], '\n', target_texts[i])

38429
Alice was beginning  
 	to get very tired of

lice was beginning t 
 	o get very tired of 

ice was beginning to 
 	 get very tired of s

ce was beginning to  
 	get very tired of si

e was beginning to g 
 	et very tired of sit

 was beginning to ge 
 	t very tired of sitt

was beginning to get 
 	 very tired of sitti

as beginning to get  
 	very tired of sittin

s beginning to get v 
 	ery tired of sitting

 beginning to get ve 
 	ry tired of sitting 



## Build vocab

In [7]:
all_texts = target_texts + input_texts
vocab_to_int, int_to_vocab = build_vocab(all_texts)
np.savez('vocab-{}', vocab_to_int=vocab_to_int, int_to_vocab=int_to_vocab)

In [8]:
input_characters = sorted(list(vocab_to_int))
target_characters = sorted(list(vocab_to_int))
num_encoder_tokens = len(input_characters)
num_decoder_tokens = len(target_characters)
max_encoder_seq_length = max([len(txt) for txt in input_texts]) + 2 # For '\t' and '\n'
max_decoder_seq_length = max([len(txt) for txt in target_texts]) + 2

In [9]:
print('Number of samples:', len(input_texts))
print('Number of unique input tokens:', num_encoder_tokens)
print('Number of unique output tokens:', num_decoder_tokens)
print('Max sequence length for inputs:', max_encoder_seq_length)
print('Max sequence length for outputs:', max_decoder_seq_length)

Number of samples: 38429
Number of unique input tokens: 67
Number of unique output tokens: 67
Max sequence length for inputs: 22
Max sequence length for outputs: 24


In [10]:
vocab_to_int # Some special chars need to be removed TODO: Data cleaning

{'\t': 2,
 '\n': 3,
 ' ': 1,
 '!': 57,
 '"': 60,
 "'": 26,
 '(': 30,
 ')': 31,
 ',': 23,
 '-': 42,
 '.': 51,
 ':': 18,
 ';': 37,
 '?': 55,
 'A': 27,
 'B': 63,
 'C': 41,
 'D': 49,
 'E': 35,
 'F': 62,
 'G': 46,
 'H': 52,
 'I': 50,
 'J': 65,
 'K': 40,
 'L': 48,
 'M': 47,
 'N': 45,
 'O': 38,
 'P': 43,
 'Q': 64,
 'R': 33,
 'S': 56,
 'T': 39,
 'U': 53,
 'UNK': 0,
 'V': 34,
 'W': 32,
 'Y': 36,
 'Z': 54,
 '[': 66,
 'a': 21,
 'b': 16,
 'c': 19,
 'd': 12,
 'e': 7,
 'f': 13,
 'g': 6,
 'h': 17,
 'i': 11,
 'j': 44,
 'k': 25,
 'l': 28,
 'm': 29,
 'n': 15,
 'o': 5,
 'p': 22,
 'q': 58,
 'r': 9,
 's': 14,
 't': 4,
 'u': 24,
 'v': 8,
 'w': 20,
 'x': 59,
 'y': 10,
 'z': 61}

In [11]:
int_to_vocab

{0: 'UNK',
 1: ' ',
 2: '\t',
 3: '\n',
 4: 't',
 5: 'o',
 6: 'g',
 7: 'e',
 8: 'v',
 9: 'r',
 10: 'y',
 11: 'i',
 12: 'd',
 13: 'f',
 14: 's',
 15: 'n',
 16: 'b',
 17: 'h',
 18: ':',
 19: 'c',
 20: 'w',
 21: 'a',
 22: 'p',
 23: ',',
 24: 'u',
 25: 'k',
 26: "'",
 27: 'A',
 28: 'l',
 29: 'm',
 30: '(',
 31: ')',
 32: 'W',
 33: 'R',
 34: 'V',
 35: 'E',
 36: 'Y',
 37: ';',
 38: 'O',
 39: 'T',
 40: 'K',
 41: 'C',
 42: '-',
 43: 'P',
 44: 'j',
 45: 'N',
 46: 'G',
 47: 'M',
 48: 'L',
 49: 'D',
 50: 'I',
 51: '.',
 52: 'H',
 53: 'U',
 54: 'Z',
 55: '?',
 56: 'S',
 57: '!',
 58: 'q',
 59: 'x',
 60: '"',
 61: 'z',
 62: 'F',
 63: 'B',
 64: 'Q',
 65: 'J',
 66: '['}

In [12]:
len(int_to_vocab)

67

# Prepare training data

## Train/test split

In [13]:
# Split the data into training and testing sentences
input_texts, test_input_texts, target_texts, test_target_texts  = train_test_split(input_texts, target_texts, test_size = 0.15, random_state = 42)

## Vectorize data

## Train data

In [14]:
encoder_input_data, decoder_input_data, decoder_target_data = vectorize_data(input_texts=input_texts,
                                                                             target_texts=target_texts, 
                                                                             max_encoder_seq_length=max_encoder_seq_length, 
                                                                             num_encoder_tokens=num_encoder_tokens, 
                                                                             vocab_to_int=vocab_to_int)

In [15]:
print(encoder_input_data.shape)
print(decoder_target_data.shape)

(32664, 22)
(32664, 22, 67)


## Test data

In [16]:
test_encoder_input_data, test_decoder_input_data, test_decoder_target_data = vectorize_data(input_texts=test_input_texts,
                                                                                            target_texts=test_target_texts, 
                                                                                            max_encoder_seq_length=max_encoder_seq_length, 
                                                                                            num_encoder_tokens=num_encoder_tokens, 
                                                                                            vocab_to_int=vocab_to_int)

# Encoder-decoder model

In [17]:

latent_dim = 256  # Latent dimensionality of the encoding space.

In [18]:
model, encoder_model, decoder_model = build_model(latent_dim=latent_dim, num_encoder_tokens=num_encoder_tokens)

[<tf.Tensor 'concatenate_1/concat:0' shape=(?, 512) dtype=float32>, <tf.Tensor 'concatenate_2/concat:0' shape=(?, 512) dtype=float32>]
Tensor("lstm_2/transpose_2:0", shape=(?, ?, 512), dtype=float32)
Tensor("bidirectional_1/concat:0", shape=(?, ?, 512), dtype=float32)
attention Tensor("attention/truediv:0", shape=(?, ?, ?), dtype=float32)
encoder-decoder  model:
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, None)         0                                            
__________________________________________________________________________________________________
embedding_1 (Embedding)         (None, None, 67)     4489        input_1[0][0]                    
__________________________________________________________________________________________________
input_2 (InputLayer)            (None, No

/home/elsallab/Work/cod/READ/utils.py:458: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=[<tf.Tenso...)`
  encoder_model = Model(input=encoder_inputs, output=[encoder_outputs] + encoder_states)


# Training

In [19]:
batch_size = 64  # Batch size for training.
epochs = 20  
lr = 0.01

# Learning rate decay

In [20]:
model.compile(optimizer=optimizers.Adam(lr=lr), loss='categorical_crossentropy', metrics=['categorical_accuracy'])

In [21]:
#filepath="weights-improvement-{epoch:02d}-{val_categorical_accuracy:.2f}.hdf5"
filepath="best_model.hdf5" # Save only the best model for inference step, as saving the epoch and metric might confuse the inference function which model to use
checkpoint = ModelCheckpoint(filepath, monitor='val_categorical_accuracy', verbose=1, save_best_only=True, mode='max')
tbCallBack = TensorBoard(log_dir='./Graph', histogram_freq=0, write_graph=True, write_images=True)
callbacks_list = [checkpoint, tbCallBack]
#callbacks_list = [checkpoint, tbCallBack, lrate]



In [22]:
def exp_decay(epoch):
    initial_lrate = 0.1
    k = 0.1
    lrate = initial_lrate * np.exp(-k*epoch)
    return lrate
lrate = LearningRateScheduler(exp_decay)
#lr = 0

In [23]:
def step_decay(epoch):
    initial_lrate = 0.1
    drop = 0.5
    epochs_drop = 10.0
    lrate = initial_lrate * math.pow(drop, math.floor((1+epoch)/epochs_drop))
    return lrate
lrate = LearningRateScheduler(step_decay)
#lr = 0

In [24]:
#callbacks_list.append(lrate)

In [25]:
model.fit([encoder_input_data, decoder_input_data], decoder_target_data,
          #validation_data = ([test_encoder_input_data, test_decoder_input_data], test_decoder_target_data),
          batch_size=batch_size,
          epochs=epochs,
          callbacks=callbacks_list,
          validation_split=0.1,
          shuffle=True)

Train on 29397 samples, validate on 3267 samples
Epoch 1/20
29397/29397 [==============================] - 46s 2ms/step - loss: 1.7658 - categorical_accuracy: 0.4581 - val_loss: 1.1746 - val_categorical_accuracy: 0.5999

Epoch 00001: val_categorical_accuracy improved from -inf to 0.59986, saving model to best_model.hdf5


/opt/anaconda3/lib/python3.6/site-packages/keras/engine/network.py:872: UserWarning: Layer lstm_2 was passed non-serializable keyword arguments: {'initial_state': [<tf.Tensor 'concatenate_1/concat:0' shape=(?, 512) dtype=float32>, <tf.Tensor 'concatenate_2/concat:0' shape=(?, 512) dtype=float32>]}. They will not be included in the serialized model (and thus will be missing at deserialization time).
  '. They will not be included '


Epoch 2/20
29397/29397 [==============================] - 44s 2ms/step - loss: 0.9957 - categorical_accuracy: 0.6511 - val_loss: 0.8747 - val_categorical_accuracy: 0.6859

Epoch 00002: val_categorical_accuracy improved from 0.59986 to 0.68591, saving model to best_model.hdf5
Epoch 3/20
29397/29397 [==============================] - 44s 2ms/step - loss: 0.7647 - categorical_accuracy: 0.7185 - val_loss: 0.7218 - val_categorical_accuracy: 0.7327

Epoch 00003: val_categorical_accuracy improved from 0.68591 to 0.73274, saving model to best_model.hdf5
Epoch 4/20
29397/29397 [==============================] - 45s 2ms/step - loss: 0.6173 - categorical_accuracy: 0.7627 - val_loss: 0.6275 - val_categorical_accuracy: 0.7602

Epoch 00004: val_categorical_accuracy improved from 0.73274 to 0.76022, saving model to best_model.hdf5
Epoch 5/20
29397/29397 [==============================] - 44s 2ms/step - loss: 0.5332 - categorical_accuracy: 0.7885 - val_loss: 0.5585 - val_categorical_accuracy: 0.7835



In [26]:
encoder_model.save('encoder_model.hdf5')
decoder_model.save('decoder_model.hdf5')

/opt/anaconda3/lib/python3.6/site-packages/keras/engine/network.py:872: UserWarning: Layer lstm_2 was passed non-serializable keyword arguments: {'initial_state': [<tf.Tensor 'input_4:0' shape=(?, 512) dtype=float32>, <tf.Tensor 'input_5:0' shape=(?, 512) dtype=float32>]}. They will not be included in the serialized model (and thus will be missing at deserialization time).
  '. They will not be included '


# Inference

In [28]:
# Sample output from train data
decoded_sentences = []
target_texts_ =  []
for seq_index in range(len(input_texts)):
    # Take one sequence (part of the training set)
    # for trying out decoding.
    input_text = input_texts[seq_index]
    target_text = target_texts[seq_index][1:-1]

    encoder_input_data, decoder_input_data, decoder_target_data = vectorize_data(input_texts=[input_text],
                                                                                 target_texts=[target_text], 
                                                                                 max_encoder_seq_length=max_encoder_seq_length, 
                                                                                 num_encoder_tokens=num_encoder_tokens, 
                                                                                 vocab_to_int=vocab_to_int)    

    input_seq = encoder_input_data
    #target_seq = np.argmax(decoder_target_data, axis=-1)
    #print(target_seq)
    decoded_sentence, _ = decode_sequence(input_seq, encoder_model, decoder_model, num_decoder_tokens, max_encoder_seq_length, int_to_vocab, vocab_to_int)
    print('-')
    print('Input sentence:', input_text)
    print('GT sentence:', target_text)
    print('Decoded sentence:', decoded_sentence)
    #results.write(' | ' + input_text + ' | ' + target_text.strip() + ' | ' + decoded_sentence + ' | \n')
    decoded_sentences.append(decoded_sentence)
    #corrected_sentences.append(corrected_sentence)
    #corrected_input_sentences.append(corrected_input_sentence)
    target_texts_.append(target_text)




-
Input sentence: couldn't help it,' s
GT sentence: aid Five, in a sulky
Decoded sentence: aid Five in a s,mme
-
Input sentence: atched the White Rab
GT sentence: bit as he fumbled ov
Decoded sentence: bit as he fumbled ov
-
Input sentence: d a little animal (s
GT sentence: he couldn't guess of
Decoded sentence: he couldn't guess (f
-
Input sentence:  seeing the Cheshire
GT sentence:  Cat sitting on a bo
Decoded sentence:  Cat sitting on a bo
-
Input sentence: rld would go round a
GT sentence:  deal faster than it
Decoded sentence:  deal faster than th
-
Input sentence:  would EVER happen i
GT sentence: n a natural way agai
Decoded sentence: n a natural way agai
-
Input sentence:  using the ink, that
GT sentence:  was trickling down 
Decoded sentence:  it was too da,k hig
-
Input sentence: ff, and she swam nea
GT sentence: rer to make out what
Decoded sentence: re, on ther moment 
-
Input sentence: icers: but the Hatte
GT sentence: r was out of sight b
Decoded sentence: r was:out of si

-
Input sentence: rms folded, frowning
GT sentence:  like a thunderstorm
Decoded sentence:  the left ,hrough th
-
Input sentence:  say "HOW DOTH THE L
GT sentence: ITTLE BUSY BEE," but
Decoded sentence: ITTLE"BUSY BEE but
-
Input sentence: executions I have or
GT sentence: dered'; and she walk
Decoded sentence: dered about' said t
-
Input sentence: d and a large fan in
GT sentence:  the other: he came 
Decoded sentence:  the other he came 
-
Input sentence: ever was so ordered 
GT sentence: about in all my life
Decoded sentence: about her arm after
-
Input sentence: d in a deep voice, '
GT sentence: What are tarts made 
Decoded sentence: What are tarts ma,e 
-
Input sentence: must manage the best
GT sentence:  way you can;--but I
Decoded sentence:  way you canbut I
-
Input sentence: ere were doors all r
GT sentence: ound the hall, but t
Decoded sentence: etch her head must 
-
Input sentence:  the garden at once;
GT sentence:  but, alas for poor 
Decoded sentence:  but alas began wo;
-


-
Input sentence: te that down,' the K
GT sentence: ing said to the jury
Decoded sentence: ing sain to ,he jury
-
Input sentence: Of course they were'
GT sentence: , said the Dormouse;
Decoded sentence:  said without openi
-
Input sentence: I do wish they WOULD
GT sentence:  put their heads dow
Decoded sentence:  MARMALD twist itsel
-
Input sentence: it had finished this
GT sentence:  short speech, they 
Decoded sentence:  short speech sister
-
Input sentence: se words were follow
GT sentence: ed by a very long si
Decoded sentence: ed and make out what
-
Input sentence: he said to herself, 
GT sentence: and shouted out, 'Yo
Decoded sentence: 'that she had not , 
-
Input sentence:  of hands at this: i
GT sentence: t was the first real
Decoded sentence: t was the first r:al
-
Input sentence: ldn't have put it in
GT sentence:  with the bread-knif
Decoded sentence:  with the lobsters 
-
Input sentence: you like,' said the 
GT sentence: Footman, and began w
Decoded sentence: Footman,and beg

-
Input sentence: his arms and frownin
GT sentence: g at the cook till h
Decoded sentence: g at the mushroom fo
-
Input sentence: tle toss of her head
GT sentence:  to keep back the wa
Decoded sentence:  to keep back the wa
-
Input sentence: rious child was very
GT sentence:  fond of pretending 
Decoded sentence:  off on off punny i
-
Input sentence: use had closed its e
GT sentence: yes by this time, an
Decoded sentence: yes by this time an
-
Input sentence: ld be quite absurd f
GT sentence: or her to carry it f
Decoded sentence: or her to carry it f
-
Input sentence: od deal: this firepl
GT sentence: ace is narrow, to be
Decoded sentence: able in:such convers
-
Input sentence: he door and found th
GT sentence: at it led into a sma
Decoded sentence: e little before she 
-
Input sentence: e had grown in the l
GT sentence: ast few minutes, and
Decoded sentence: ong say this mount 
-
Input sentence: and they don't seem 
GT sentence: to have any rules in
Decoded sentence: to have any rule

-
Input sentence: st turned sulky, and
GT sentence:  would only say, 'I 
Decoded sentence:  would not opol,of t
-
Input sentence: ' remarked the King,
GT sentence:  'or I'll have you e
Decoded sentence:  and the White Rabb,
-
Input sentence: oment to be lost: aw
GT sentence: ay went Alice like t
Decoded sentence:  you were like a:sta
-
Input sentence: he Owl had the dish 
GT sentence: as its share of the 
Decoded sentence: a was shrinking away
-
Input sentence: You'll get used to i
GT sentence: t in time,' said the
Decoded sentence: t in time' said the
-
Input sentence: able for it, she fou
GT sentence: nd she could not pos
Decoded sentence: nd the righ, silent 
-
Input sentence: rthumbria, declared 
GT sentence: for him: and even St
Decoded sentence: to her ea, and when
-
Input sentence:  I can't show it you
GT sentence:  myself,' the Mock T
Decoded sentence:  may come your head 
-
Input sentence: sh, who wanted leade
GT sentence: rs, and had been of 
Decoded sentence: rs, and had bee

...

-
Input sentence: ed deeply, and began
GT sentence: , in a voice sometim
Decoded sentence:  in a vo,ce she was
-
Input sentence: up one of the legs o
GT sentence: f the table, but it 
Decoded sentence: f the table but it 
-
Input sentence: -Don't choke him--Ho
GT sentence: w was it, old fellow
Decoded sentence: - was a very won-- t
-
Input sentence: tman was gone, and t
GT sentence: he other was sitting
Decoded sentence: he other was ,itches
-
Input sentence: case it would be ver
GT sentence: y likely to eat her 
Decoded sentence: y likely three littl
-
Input sentence: Here the Dormouse sh
GT sentence: ook itself, and bega
Decoded sentence: e could and the oth
-
Input sentence: as well say,' added 
GT sentence: the Dormouse, who se
Decoded sentence: the March H,re 'whe
-
Input sentence: d silence instantly,
GT sentence:  and Alice thought t
Decoded sentence:  and Alice thought ,
-
Input sentence: couraged to ask any 
GT sentence: more questions about
Decoded sentence: making such a thi

-
Input sentence: st her foot, that th
GT sentence: ere was hardly room 
Decoded sentence: ey were lit,le room 
-
Input sentence: e looked all round t
GT sentence: he table, but there 
Decoded sentence: he same to be a fall
-
Input sentence: wo, looking for them
GT sentence: , and then quietly m
Decoded sentence:  a, the hoppow of pr
-
Input sentence: ecked himself sudden
GT sentence: ly: the others looke
Decoded sentence: ly then the other v
-
Input sentence: nd the table, but th
GT sentence: ere was nothing on i
Decoded sentence: ere was noth,ng on i
-
Input sentence: , and she jumped up 
GT sentence: on to her feet in a 
Decoded sentence: ,nd drew a few musta
-
Input sentence: d he got up very sul
GT sentence: kily and crossed ove
Decoded sentence: kily and crossed ove
-
Input sentence:  as far down the chi
GT sentence: mney as she could, a
Decoded sentence: mney as she could a
-
Input sentence: ueen, in a shrill, l
GT sentence: oud voice, and the t
Decoded sentence: ying,down on on

-
Input sentence:  her knee, and the b
GT sentence: right eager eyes wer
Decoded sentence: rearon of,the creatu
-
Input sentence: ll the jurymen on to
GT sentence:  the heads of the cr
Decoded sentence:  the heads of the ca
-
Input sentence: ad not gone much far
GT sentence: ther before she came
Decoded sentence: ther before she came
-
Input sentence: fetch the executione
GT sentence: r myself,' said the 
Decoded sentence: r means and fanned 
-
Input sentence: I don't like the loo
GT sentence: k of it at all,' sai
Decoded sentence: k of it at all' sai
-
Input sentence:  and the Hatter were
GT sentence:  having tea at it: a
Decoded sentence:  'sitting on the mis
-
Input sentence: on the English coast
GT sentence:  you find a number o
Decoded sentence:  be in a nice little
-
Input sentence:  me left to make ONE
GT sentence:  respectable person!
Decoded sentence:  remarks and the po
-
Input sentence: tened up at the thou
GT sentence: ght that she was now
Decoded sentence: ght that she was

-
Input sentence: re seemed to be no c
GT sentence: hance of getting her
Decoded sentence: hance of getting her
-
Input sentence: She was moving them 
GT sentence: about as she spoke, 
Decoded sentence: about as she spoke 
-
Input sentence:  the executioner mys
GT sentence: elf,' said the King 
Decoded sentence: elf' said the King
-
Input sentence:  she were saying les
GT sentence: sons, and began to r
Decoded sentence: sons and began to r
-
Input sentence: r down the chimney a
GT sentence: s she could, and wai
Decoded sentence: nd stupid for life a
-
Input sentence: : she thought it mus
GT sentence: t be the right house
Decoded sentence: : on her head must b
-
Input sentence: ff together, Alice h
GT sentence: eard the King say in
Decoded sentence: eard the Ki,g 'that
-
Input sentence:  teacups as the Marc
GT sentence: h Hare and his frien
Decoded sentence: h Hare and her hands
-
Input sentence: rp little chin into 
GT sentence: Alice's shoulder as 
Decoded sentence: find that she wasn

KeyboardInterrupt: 

# Visualize attention

In [ ]:
for seq_index in range(100):

    target_text = target_texts[seq_index][1:-1]
    text = input_texts[seq_index]
    decoded_sentence = visualize_attention(text, encoder_model, decoder_model, max_encoder_seq_length, num_decoder_tokens, vocab_to_int, int_to_vocab)
    print('-')
    print('Input sentence:', text)
    print('GT sentence:', target_text)
    print('Decoded sentence:', decoded_sentence)   


# Test - Short inference

In [ ]:
# Sample output from train data
decoded_sentences = []
target_texts_ =  []
corrected_sentences = []
corrected_input_sentences = []
results = open('RESULTS.md', 'w')
results.write('|OCR sentence|GT sentence|Decoded sentence|\n')
results.write('|------------|-----------|----------------|\n')
for seq_index in range(len(test_input_texts)):
    # Take one sequence (part of the training set)
    # for trying out decoding.
    input_text = test_input_texts[seq_index]
    target_text = test_target_texts[seq_index][1:-1]

    encoder_input_data, decoder_input_data, decoder_target_data = vectorize_data(input_texts=[input_text],
                                                                                 target_texts=[target_text], 
                                                                                 max_encoder_seq_length=max_encoder_seq_length, 
                                                                                 num_encoder_tokens=num_encoder_tokens, 
                                                                                 vocab_to_int=vocab_to_int)    

    input_seq = encoder_input_data
    #target_seq = np.argmax(decoder_target_data, axis=-1)
    #print(target_seq)
    decoded_sentence, _ = decode_sequence(input_seq, encoder_model, decoder_model, num_decoder_tokens, max_encoder_seq_length, int_to_vocab, vocab_to_int)
    print('-')
    print('Input sentence:', input_text)
    print('GT sentence:', target_text)
    print('Decoded sentence:', decoded_sentence)
    results.write(' | ' + input_text + ' | ' + target_text.strip() + ' | ' + decoded_sentence + ' | \n')
    decoded_sentences.append(decoded_sentence)
    #corrected_sentences.append(corrected_sentence)
    #corrected_input_sentences.append(corrected_input_sentence)
    target_texts_.append(target_text)


encoder_input_data = vectorize_data(input_texts=input_texts, max_encoder_seq_length=max_encoder_seq_length, num_encoder_tokens=num_encoder_tokens, vocab_to_int=vocab_to_int)
    
results.close() 

-
Input sentence: n, so that altogethe
GT sentence: r, for the first min
Decoded sentence: r,about her eyes wer
-
Input sentence:  she found herself f
GT sentence: alling down a very d
Decoded sentence: or some minutes it s
-
Input sentence:  him with them,' the
GT sentence:  Mock Turtle said: '
Decoded sentence:  Mock Turtle s,id wi
-
Input sentence: ttle glass box that 
GT sentence: was lying under the 
Decoded sentence: was lying under the 
-
Input sentence: make personal remark
GT sentence: s,' Alice said with 
Decoded sentence: ' Alice said very p
-
Input sentence: s terribly frightene
GT sentence: d all the time at th
Decoded sentence: d all the time at th
-
Input sentence: use I'm on the same 
GT sentence: side of the door as 
Decoded sentence: do' said the Duches
-
Input sentence: last the Caterpillar
GT sentence:  took the hookah out
Decoded sentence:  took the hookah out
-
Input sentence:  walking off to othe
GT sentence: r parts of the groun
Decoded sentence: r hearing anyth

-
Input sentence:  Alice, 'I've often 
GT sentence: seen them at dinn--'
Decoded sentence: the Du,hess the two 
-
Input sentence: oice along--'Catch h
GT sentence: im, you by the hedge
Decoded sentence: is heart --e hed se
-
Input sentence: ice quietly said, ju
GT sentence: st as if it had come
Decoded sentence: bsed at it was c,rta
-
Input sentence:  soon found an oppor
GT sentence: tunity of taking it 
Decoded sentence: tunity of your till 
-
Input sentence: So they got their ta
GT sentence: ils fast in their mo
Decoded sentence: nish' thought Alice
-
Input sentence: ed the King, 'or I'l
GT sentence: l have you executed.
Decoded sentence: l me the ju,ybox wi
-
Input sentence: ing larger and small
GT sentence: er, and being ordere
Decoded sentence:  before 'and that h
-
Input sentence: e the whole party lo
GT sentence: ok so grave and anxi
Decoded sentence: st somebody to get r
-
Input sentence:  just as well say,' 
GT sentence: added the March Hare
Decoded sentence: the March Hare ad

-
Input sentence:  kept on good terms 
GT sentence: with him, he'd do al
Decoded sentence: him and she did not
-
Input sentence: o the company genera
GT sentence: lly, 'You are all pa
Decoded sentence: cle and was Yo a lo
-
Input sentence:  and took the thimbl
GT sentence: e, looking as solemn
Decoded sentence: e and looking at ev
-
Input sentence: ch out of the way to
GT sentence:  hear the Rabbit say
Decoded sentence:  her ear her once mo
-
Input sentence: said these words her
GT sentence:  foot slipped, and i
Decoded sentence: self sofe to her on
-
Input sentence: self from being run 
GT sentence: over; and the moment
Decoded sentence: on to mave out the m
-
Input sentence: e puzzled, but she t
GT sentence: hought there was no 
Decoded sentence: hought th,re was not
-
Input sentence: bbed again (or grunt
GT sentence: ed, it was impossibl
Decoded sentence: ing itself(if the D
-
Input sentence: eply, and drew the b
GT sentence: ack of one flapper a
Decoded sentence: lash,of voices and

-
Input sentence: lar that Dormouse,' 
GT sentence: the Queen shrieked o
Decoded sentence: the Queen said th, Q
-
Input sentence: a large cauldron whi
GT sentence: ch seemed to be full
Decoded sentence: ch sue it mushroom 
-
Input sentence: ee stood near the en
GT sentence: trance of the garden
Decoded sentence: courage and went on
-
Input sentence:  can't explain MYSEL
GT sentence: F, I'm afraid, sir' 
Decoded sentence:  IT THE LITTLE make 
-
Input sentence: ing at it uneasily, 
GT sentence: shaking it every now
Decoded sentence: 'I wish they were ,l
-
Input sentence: ate a little bit, an
GT sentence: d said anxiously to 
Decoded sentence: d said anxiously,to 
-
Input sentence: spered, 'that it's d
GT sentence: one by everybody min
Decoded sentence: ink gi,l it was good
-
Input sentence: raid, but you might 
GT sentence: catch a bat, and tha
Decoded sentence: as s,e came to begin
-
Input sentence:  continued the Hatte
GT sentence: r, 'I cut some more 
Decoded sentence: r cut on sittin

-
Input sentence: people here; the gre
GT sentence: at wonder is, that t
Decoded sentence: at on the c;eatures
-
Input sentence: ut which were the tw
GT sentence: o sides of it; and a
Decoded sentence: is silent and looke
-
Input sentence: d for some time with
GT sentence: out hearing anything
Decoded sentence:  its arms folder an
-
Input sentence: once more the shriek
GT sentence:  of the Gryphon, the
Decoded sentence:  like a stalk and a 
-
Input sentence: very good advice, (t
GT sentence: hough she very seldo
Decoded sentence: ook Alice very s,e(h
-
Input sentence: his speech caused a 
GT sentence: remarkable sensation
Decoded sentence: pause that for tell 
-
Input sentence:  the jurymen on to t
GT sentence: he heads of the crow
Decoded sentence: he hedgehog have bee
-
Input sentence: ed at the jury-box, 
GT sentence: and saw that, in her
Decoded sentence: 'that I haven-t b,e
-
Input sentence: ile, finding that no
GT sentence: thing more happened,
Decoded sentence: w h,ppened she ha

...

-
Input sentence: eplied Alice; 'and I
GT sentence:  wish you wouldn't k
Decoded sentence: 'll have you;will yo
-
Input sentence: w better'; and this 
GT sentence: Alice would not allo
Decoded sentence: look over;with larg 
-
Input sentence: ned out, and was goi
GT sentence: ng to give the hedge
Decoded sentence: ng to g,ve throwing 
-
Input sentence: , I can't show it yo
GT sentence: u myself,' the Mock 
Decoded sentence: , myself' the Mock 
-
Input sentence:  Alice, swallowing d
GT sentence: own her anger as wel
Decoded sentence: own he,self and the
-
Input sentence: ic archbishop of Can
GT sentence: terbury, found it ad
Decoded sentence: e if he doesn't get
-
Input sentence: uted out, 'You'd bet
GT sentence: ter not do that agai
Decoded sentence: ter did ,ot like tha
-
Input sentence: directed at all,' sa
GT sentence: id the White Rabbit;
Decoded sentence: id the White Ra,bit
-
Input sentence: low with its head, i
GT sentence: t WOULD twist itself
Decoded sentence: f I'm gring' sai,

-
Input sentence:  set about it; and w
GT sentence: hile she was peering
Decoded sentence: hile she was ;ow pos
-
Input sentence: rs all joined in cho
GT sentence: rus, 'Yes, please do
Decoded sentence: uld 'buce in the mid
-
Input sentence: coming to look for h
GT sentence: er, and she trembled
Decoded sentence: er and she trembled
-
Input sentence: muddle their slates'
GT sentence: ll be in before the 
Decoded sentence:  behind her about f
-
Input sentence:  up this morning, bu
GT sentence: t I think I must hav
Decoded sentence: t I shall here o,t o
-
Input sentence: generally a ridge or
GT sentence:  furrow in the way w
Decoded sentence:  never of a well as 
-
Input sentence: he Gryphon said, in 
GT sentence: a rather offended to
Decoded sentence: the same side ,he s
-
Input sentence: nimal (she couldn't 
GT sentence: guess of what sort i
Decoded sentence: could (nly hear the 
-
Input sentence:  had begun to think 
GT sentence: that very few things
Decoded sentence: this was very li

-
Input sentence: know of any that do,
GT sentence: ' Alice said very po
Decoded sentence: ' Alice said very p,
-
Input sentence: r been in a court of
GT sentence:  justice before, but
Decoded sentence:  getting her toud fo
-
Input sentence:  their putting their
GT sentence:  heads down and sayi
Decoded sentence:  heads down and sayi
-
Input sentence: VERY much out of the
GT sentence:  way to hear the Rab
Decoded sentence:  had to be after thi
-
Input sentence:  last word with such
GT sentence:  sudden violence tha
Decoded sentence:  stuck her in such a
-
Input sentence:  don't believe it,' 
GT sentence: said the Pigeon; 'bu
Decoded sentence: said the Pigeon ,so
-
Input sentence: OF ITS WAISTCOAT-POC
GT sentence: KET, and looked at i
Decoded sentence: E I'm Mabel I'-l s
-
Input sentence: es and looked anxiou
GT sentence: sly round, to make o
Decoded sentence: sly garden change a
-
Input sentence: tart, custard, pine-
GT sentence: apple, roast turkey,
Decoded sentence: thro,e and t,ough

-
Input sentence: hat to do, and in de
GT sentence: spair she put her ha
Decoded sentence: al such a,please si
-
Input sentence: ike a Jack-in-the-bo
GT sentence: x, and up I goes lik
Decoded sentence: ght usuall- I-are-p 
-
Input sentence:  round it: there was
GT sentence:  a dispute going on 
Decoded sentence:  now a di:pution a g
-
Input sentence: the English coast yo
GT sentence: u find a number of b
Decoded sentence: u were nice like a s
-
Input sentence: window, and on it (a
GT sentence: s she had hoped) a f
Decoded sentence: s shou,der as he s(i
-
Input sentence: piece of rudeness wa
GT sentence: s more than Alice co
Decoded sentence: iting by the poor Aa
-
Input sentence: l its feet at once, 
GT sentence: with a yelp of delig
Decoded sentence: with a sigh 'we'l,o
-
Input sentence:  Majesty,' the Hatte
GT sentence: r began, in a trembl
Decoded sentence: r began,in a the ci
-
Input sentence: s all this time, sat
GT sentence:  down again very sad
Decoded sentence: h as he spide o,

-
Input sentence:  about among those b
GT sentence: eds of bright flower
Decoded sentence: eginning of bright f
-
Input sentence: her lessons in the s
GT sentence: choolroom, and thoug
Decoded sentence: ubbrock out that one
-
Input sentence: t day,' said the Moc
GT sentence: k Turtle: 'nine the 
Decoded sentence: k Tur,le 'why if a
-
Input sentence: ou can draw water ou
GT sentence: t of a water-well,' 
Decoded sentence: t of a waterwell' 
-
Input sentence: ed, she was appealed
GT sentence:  to by all three to 
Decoded sentence:  d,wn to them to be 
-
Input sentence: ust, and walked off;
GT sentence:  the Dormouse fell a
Decoded sentence:  an, the Dormouse f;
-
Input sentence: ers that you have ju
GT sentence: st been reading abou
Decoded sentence: mber in by mire bran
-
Input sentence: d thoughts she decid
GT sentence: ed to remain where s
Decoded sentence: s and stranged a lit
-
Input sentence:  once, with a yelp o
GT sentence: f delight, and rushe
Decoded sentence: f del,ght and rus

In [ ]:

for seq_index in range(100):
    target_text = test_target_texts[seq_index][1:-1]
    text = test_input_texts[seq_index]

    decoded_sentence = visualize_attention(text, encoder_model, decoder_model, max_encoder_seq_length, num_decoder_tokens, vocab_to_int, int_to_vocab)
    print('-')
    print('Input sentence:', text)
    print('GT sentence:', target_text)
    print('Decoded sentence:', decoded_sentence)  


# Decode single sentence as moving window

In [ ]:
seq_index = 100
text = input_texts[seq_index]
input_texts, target_texts = generate_lm_data(text, in_seq_len, out_seq_len)
for input_text, target_text in enumerate(zip(input_texts, target_texts)):
    print('-')
    print('Input sentence:', input_text)
    print('GT sentence:', target_text)
    decoded_sentence = visualize_attention(input_text, encoder_model, decoder_model, max_encoder_seq_length, num_decoder_tokens, vocab_to_int, int_to_vocab)
    print('Decoded sentence:', decoded_sentence)  